## Task 1

### Animation

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
from dataclasses import dataclass
from typing import List
from matplotlib.animation import FuncAnimation

FPS = 60  # increase to make animation slower
t_start = -5.0
t_end = 5.0
frames = int((t_end - t_start) * FPS)


def fx(t):
    return 3*np.cos(2*t)*np.cos(t) + 0.82


def fy(t):
    return 3*np.cos(2*t)*np.sin(t) + 0.82


# function computes current sim time by frame number
def t(i):
    return t_start + i / FPS

In [ ]:
!pip3 install matplotlib numpy PyQt5

In [ ]:

# class take core of storing data points we computed in animation
@dataclass
class TracePoint:
    x: float
    y: float
    t: float

    vel: np.array
    acc: np.array

    @property
    def accn(self):
        # nothing special, just normal acceleration as difference
        return self.acc - self.acct

    @property
    def acct(self):
        # tangential acceleration is aligned with velocity vector
        acct = np.dot(self.acc, self.vel / np.linalg.norm(self.vel))
        return acct * self.vel / np.linalg.norm(self.vel)

    @property
    def k(self):
        # in original formula there are derivatives,
        # but in our sense they are just acceleration and veloctiy
        return np.linalg.norm(self.acc) / (np.sqrt(1 + self.vel.dot(self.vel))) ** 3

    @property
    def osculating_center(self):
        # i'm not a genius in math, but i think this is correct
        # http://mathonline.wikidot.com/the-osculating-circle-at-a-point-on-a-curve
        radius = 1 / self.k
        # find center of osculating center
        tan = self.vel / np.linalg.norm(self.vel)  # tangent
        b = np.cross(self.vel, self.acc)  # binormal
        n = np.cross(b, tan)  # normal
        n = n / np.linalg.norm(n)
        return np.array([self.x, self.y, 0]) + radius * n

In [ ]:

# nothing will be interesting later, just initalization of plot

trace: List[TracePoint] = []

fig, ax = plt.subplots(figsize=(10, 10))
ax.set(xlim=(-30, 30), ylim=(-30, 30))
ax.set_aspect("equal")
ax.grid()


line = ax.plot([], [], color="k", lw=2)[0]
# display velocity vector
vel = ax.arrow(0, 0, 0, 0, head_width=0.5, head_length=0.5, color="r", label="vel")
acc = ax.arrow(0, 0, 0, 0, head_width=0.5, head_length=0.5, color="b", label="acc")
acct = ax.arrow(
    0,
    0,
    0,
    0,
    head_width=0.5,
    head_length=0.5,
    color="black",
    label="tangential acc",
)
accn = ax.arrow(
    0,
    0,
    0,
    0,
    head_width=0.5,
    head_length=0.5,
    color="lime",
    label="normal acceleration",
)

ktext = ax.text(30, 0, "", color="k", fontsize=20)

osculatingCircle = plt.Circle((0, 0), 5, color="g", fill=False)
ax.add_patch(osculatingCircle)
ax.legend()


def animate(i):
    ti = t(i)
    trace.append(
        TracePoint(
            x=fx(ti),
            y=fy(ti),
            t=ti,
            vel = np.array([-6*np.sin(2*ti)*np.cos(ti) - 3*np.cos(2*ti)*np.sin(ti),
                            -6*np.sin(2*ti)*np.sin(ti) + 3*np.cos(2*ti)*np.cos(ti), 0]),
            acc = np.array([-15*np.cos(2*ti)*np.cos(ti) + 12*np.sin(2*ti)*np.sin(ti),
                            -15*np.cos(2*ti)*np.sin(ti) - 12*np.sin(2*ti)*np.cos(ti), 0]),
        )
    )

    last = trace[-1]
    line.set_xdata([p.x for p in trace])
    line.set_ydata([p.y for p in trace])

    vel.set_data(x=last.x, dx=last.vel[0], y=last.y, dy=last.vel[1])
    acc.set_data(x=last.x, dx=last.acc[0], y=last.y, dy=last.acc[1])
    acct.set_data(x=last.x, dx=last.acct[0], y=last.y, dy=last.acct[1])
    accn.set_data(x=last.x, dx=last.accn[0], y=last.y, dy=last.accn[1])

    osculatingCircle.set_radius(1 / last.k)
    osculatingCircle.set_center(last.osculating_center)

    ktext.set_text(f"k = {last.k:.8f}")


anim = FuncAnimation(fig, animate, interval=1, frames=frames)
anim.save("motion_task1.gif")
plt.draw()
plt.show()

### Plots

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from math import sqrt

# Define the time values
t_values = np.linspace(0, 10, 1000)  # 100 points from 0 to 10

# Replace these functions with your actual functions
def acceleration_function(t):
    return 3 * np.sqrt(9*np.cos(2*t)**2 + 16)

def velocity_function(t):
    return 3 * np.sqrt(1 + 3*np.sin(2*t)**2)

def normal_acceleration(t):
    return (9*np.sin(2*t)**2 + 15)/(np.sqrt(1 + 3*np.sin(2*t)**2))

def tangential_acceleration(t):
    return (9*np.sin(4*t))/(np.sqrt(1+3*np.sin(2*t)**2))

def curvature(t):
    return (3*np.sin(2*t)**2 + 5)/(3*((1+3*np.sin(2*t)**2)**(3/2)))

# Calculate acceleration and velocity values
acceleration_values = acceleration_function(t_values)
velocity_values = velocity_function(t_values)
tangential_acceleration_values = tangential_acceleration(t_values)
normal_acceleration_values = normal_acceleration(t_values)
curvature_values= curvature(t_values)

# Create a 3x2 grid for the plots
plt.figure(figsize=(12, 8))

# Plot 1: Acceleration vs Time
plt.subplot(3, 2, 1)
plt.plot(t_values, acceleration_values, label='Acceleration')
plt.title('Acceleration vs Time')
plt.xlabel('Time (t)')
plt.ylabel('Acceleration (a)')
plt.legend()

# Plot 2: Velocity vs Time
plt.subplot(3, 2, 2)
plt.plot(t_values, velocity_values, label='Velocity', color='orange')
plt.title('Velocity vs Time')
plt.xlabel('Time (t)')
plt.ylabel('Velocity (v)')
plt.legend()

# Plot 3: Tangenrial accel. vs Time
plt.subplot(3, 2, 3)
plt.plot(t_values, tangential_acceleration_values, label='a_t(t)', color='blue')
plt.title('Tangenrial accel. vs Time')
plt.xlabel('Time (t)')
plt.ylabel('a_t(v)')
plt.legend()

# Plot 4: Normal accel. vs Time
plt.subplot(3, 2, 4)
plt.plot(t_values, normal_acceleration_values, label='a_n(t)', color='black')
plt.title('Normal accel. vs Time')
plt.xlabel('Time (t)')
plt.ylabel('a_n(v)')
plt.legend()


# Plot 5: Curvature vs Time
plt.subplot(3, 2, 5)
plt.plot(t_values, curvature_values, label='k(t)', color='green')
plt.title('Curvature vs Time')
plt.xlabel('Time (t)')
plt.ylabel('k(v)')
plt.legend()

plt.tight_layout()
plt.show()

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from math import sqrt

# Define the time values
t_values = np.linspace(0, np.sqrt(1/12), 1000)  # 100 points from 0 to 10

# Replace these functions with your actual functions
def velocity_M(t):
    return 120*t

def total_acceleration_of_M(t):
    return np.sqrt(normal_acceleration_of_M(t)**2 + tangential_acceleration_of_M(t)**2)

def normal_acceleration_of_M(t):
    return 960*t**2

def tangential_acceleration_of_M(t):
    result = np.ones((len(t),)) * 120
    return result


# Calculate acceleration and velocity values
velocity_M_values = velocity_M(t_values)
tangential_acceleration_values_of_M = tangential_acceleration_of_M(t_values)
normal_acceleration_values_of_M = normal_acceleration_of_M(t_values)
total_acceleration_values_of_M = total_acceleration_of_M(t_values)


In [ ]:
# Create a 3x2 grid for the plots
plt.figure(figsize=(8, 5))

# Plot 1: Velocity of M vs Time
plt.plot(t_values, velocity_M_values, label='Velocity of M')
plt.title('Acceleration vs Time')
plt.xlabel('Time (t)')
plt.ylabel('Velocity of M')
plt.legend()

In [ ]:
# Create a 3x2 grid for the plots
plt.figure(figsize=(14, 5))

# Plot 1: Acceleration vs Time
plt.subplot(1, 3, 1)
plt.plot(t_values, total_acceleration_values_of_M, label='a(t) of M')
plt.title('Acceleration vs Time')
plt.xlabel('Time (t)')
plt.ylabel('a(t)')
plt.legend()

# Plot 2: Normal accel. vs Time
plt.subplot(1, 3, 2)
plt.plot(t_values, normal_acceleration_values_of_M, label='a_n(t) of M', color='black')
plt.title('Normal accel. vs Time')
plt.xlabel('Time (t)')
plt.ylabel('a_n(v)')
plt.legend()

# Plot 3: Tangenrial accel. vs Time
plt.subplot(1, 3, 3)
plt.plot(t_values, tangential_acceleration_values_of_M, label='a_t(t) of M', color='blue')
plt.title('Tangential accel. vs Time')
plt.xlabel('Time (t)')
plt.ylabel('a_t(v)')
plt.legend()

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from math import sqrt

# Define the time values
t_values = np.linspace(0, np.sqrt(1/12), 1000)  # 100 points from 0 to 10

# Replace these functions with your actual functions
def w_2(t):
    return 4*t

def w_m(t):
    return 8*t

# Calculate angular velocities
w_2_values = w_2(t_values)
w_m_values = w_m(t_values)

In [ ]:
# Create a 1x2 grid for the plots
plt.figure(figsize=(6, 4))

# Plot 1: w_2, w_m vs Time
plt.plot(t_values, w_2_values, label='w_2(t)')
plt.plot(t_values, w_m_values, label='w_M(t)')
plt.title('Angualar vel. of body 2, M vs Time')
plt.xlabel('Time (t)')
plt.legend()


## Task 2

### Animations

In [7]:
from dataclasses import dataclass
from typing import List
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
import matplotlib.patches as patches

t_start=0
t_end= np.sqrt(1/12)

# Set up the figure and axis
fig, ax = plt.subplots()
ax.set_xlim(-100, 100)
ax.set_ylim(-100, 100)



pointM, = plt.plot([], [], 'bo', markersize=8)
label = plt.text(0, 0, '', ha='left', va='center',fontsize=12)

circle1 = plt.Circle((0, 0), 40, edgecolor='black', facecolor='none')
circle2 = plt.Circle((0, 0), 30, edgecolor='black', facecolor='none')
circle3 = plt.Circle((np.cos(45)*15, np.sin(45)*15), 15, edgecolor='black', facecolor='none')
box= plt.Rectangle((40,-30),5,5,edgecolor='black',facecolor='none')

# Create the rod
line, = ax.plot([], [], 'green', lw = 2)

# Add rectangles and rod to the plot
ax.add_patch(circle1)
ax.add_patch(circle2)
ax.add_patch(circle3)
ax.add_patch(box)

# velo = ax.arrow(0, 0, 0, 0, head_width=0.5, head_length=0.5, color="r", label="vel")
# acce = ax.arrow(0, 0, 0, 0, head_width=0.5, head_length=0.5, color="b", label="acc")

def find_coordinates_at_time(arc_length_function, time):
    # Step 1: Evaluate s(t) to find the arc length
    arc_length = arc_length_function(time)
    
    # Step 2: Calculate the angle (in radians) corresponding to the traveled arc length
    theta = arc_length / radius
    
    # Step 3: Convert polar coordinates to Cartesian coordinates
    x_t = np.cos(45)*15 + radius * np.cos(theta)
    y_t = np.sin(45)*15 + radius * np.sin(theta)
    
    return x_t, y_t


def arc_length_function(t):
    # Replace this with your specific arc length function
    return 60*t**2

# position of a box
def find_position_of_box(time):
    return 0, 3 + 80*time**2

initial_coordinates = (0, 0)  # Initial coordinates of M
radius = 15  # Radius of the circle



def update(time, pointM, box, line):

    # Update M
    x_m, y_m = find_coordinates_at_time(arc_length_function, time)
    pointM.set_data(x_m, y_m)

    # Update box
    x_box, y_box = find_position_of_box(time)
    box.set_y(-y_box-30)

    # Update the position of the rod
    line.set_data([40, 40], [0, -y_box-30])

    
    return pointM, box, line


animation = FuncAnimation(fig, update, frames = np.linspace(t_start, t_end, 101), interval=50, blit=True, fargs=(pointM, box, line))

plt.title('Elliptical trammel mechanism')
plt.xlabel('X-axis')
plt.ylabel('Y-axis')
plt.gca().set_aspect('equal', adjustable='box')
animation.save("task2_anim.gif")


from IPython.display import HTML, display
display(HTML(animation.to_jshtml()))
plt.close(fig)

MovieWriter ffmpeg unavailable; using Pillow instead.


### Plots

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from math import sqrt

# Define the time values
t_values = np.linspace(0, 10, 1000)  # 100 points from 0 to 10

# Replace these functions with your actual functions
def velocity_a(t):
    return 2*np.pi*np.cos(np.pi*t/5)

def velocity_b(t):
    # Calculate numerator
    num = 18 * np.pi * np.cos(np.pi * t / 5) + 4 * np.pi * np.sin(2 * np.pi * t / 5)
    
    # Calculate denominator squared
    den_sq = 243 - 72 * np.sin(np.pi * t / 5) - 16 * np.sin(np.pi * t / 5)**2
    
    # Check if denominator is nonzero before taking square root
    return -num / np.sqrt(den_sq)


# Calculate acceleration and velocity values
velocity_a_values = velocity_a(t_values)
velocity_b_values = velocity_b(t_values)

# Create a 3x2 grid for the plots
plt.figure(figsize=(14, 5))

# Plot 1: Acceleration vs Time
plt.subplot(1, 2, 1)
plt.plot(t_values, velocity_a_values, label='v_a(t) of A')
plt.title('Velocity of A vs Time')
plt.xlabel('Time (t)')
plt.ylabel('v_a(t)')
plt.legend()

# Plot 2: Normal accel. vs Time
plt.subplot(1, 2, 2)
plt.plot(t_values, velocity_b_values, label='v_b(t) of B', color='black')
plt.title('Velocity of B vs Time')
plt.xlabel('Time (t)')
plt.ylabel('v_b(v)')
plt.legend()


## Task 3

### Animation

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation

# Function to update the position of the rectangles, the rod, and the labels
def update(num, rectA, rectB, line, pointC, labelA, labelB, labelC):
    # Update the position of rectangle A along the y-axis
    y_a = 22.5 + 10 * np.sin(np.pi*num/5)
    rectA.set_y(y_a-5)
    
    # Get the updated x and y coordinates of rectangle A
    x_a, y_a = rectA.get_xy()
    
    # Update the position of rectangle B along the x-axis
    rectB.set_x(np.sqrt(45**2 - (y_a+5)**2)-5)
    
    # Get the updated x and y coordinates of rectangle B
    x_b, y_b = rectB.get_xy()
    
    # Update the position of the rod
    line.set_data([x_a+2.5, x_b+5], [y_a+5, y_b+2.5])

    # Update the point C
    pointC.set_data((x_b+5)/3, (y_a+5)*2/3)
    
    # Update the text labels with the coordinates
    labelA.set_text('A: ({:.2f}, {:.2f})'.format(x_a+2.5, y_a+5))
    labelB.set_text('B: ({:.2f}, {:.2f})'.format(x_b+5, y_b+2.5))
    labelC.set_text('C: ({:.2f}, {:.2f})'.format((x_b+5)/3, (y_a+5)*2/3))
    
    return rectA, rectB, line, pointC, labelA, labelB, labelC

# Set up the figure and axis
fig, ax = plt.subplots()
ax.set_xlim(-50, 50)
ax.set_ylim(-50, 50)

# Create rectangle A
rectA = plt.Rectangle((-2.5, 17.5), 5, 10, fc='blue', alpha=0.5)

# Create rectangle B
rectB = plt.Rectangle((np.sqrt(45**2-22.5**2)-5, -2.5), 10, 5, fc='red', alpha=0.5)

# Create the rod
line, = ax.plot([], [], 'green', lw = 2)

# Create the coordinate labels
labelA = plt.text(0, -10, '', transform=ax.transData)
labelB = plt.text(0, -15, '', transform=ax.transData)
labelC = plt.text(0, -20, '', transform=ax.transData)
labelA.set_color("blue")
labelB.set_color("red")


# Create point C
pointC, = ax.plot([], [], 'bo', markersize=5, color='black')


# Add rectangles and rod to the plot
ax.add_patch(rectA)
ax.add_patch(rectB)

# Set up the animation
ani = animation.FuncAnimation(fig, update, frames=np.linspace(0, 10, 101),
                              interval=50, blit=True, fargs=(rectA, rectB, line, pointC, labelA, labelB, labelC))

plt.title('Elliptical trammel mechanism')
plt.xlabel('X-axis')
plt.ylabel('Y-axis')
plt.grid(True)
plt.gca().set_aspect('equal', adjustable='box')
ani.save("t3_anim.gif")

from IPython.display import HTML, display
display(HTML(ani.to_jshtml()))
plt.close(fig)


### Plots